## Importing Libraries

In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import os
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense,Conv2D,MaxPooling2D,Dropout,Flatten
from tensorflow.keras.layers import Activation
from sklearn.model_selection import train_test_split
from PIL import Image
import cv2
from zipfile import ZipFile
from warnings import filters

## File Zipping And Directory Path


In [2]:
#  image_directory="Brain_Tumer_Detection/"

image_directory="Brain_Tumor/"

# with ZipFile('/content/Brain_Tumor_Detection.zip', 'r') as zip_ref:
#     zip_ref.extractall(image_directory )

with ZipFile('/content/Brain_Tumor.zip', 'r') as zip_ref:
    zip_ref.extractall(image_directory )


# directory='/content/Brain_Tumor_Detection/Brain_Tumor_Detection/'

directory='/content/Brain_Tumor/Brain_Tumor/'

### Creating Paths

In [4]:
no_tumer_images=os.listdir(directory+'no/')
yes_tumer_images=os.listdir(directory+'yes/')
yes_dir='yes/'
no_dir='no/'
dataset=[]
labels=[]

## Preprocessing The Images

In [5]:
def preprocessing (path,sub_path,label_data):
  for i,image_name in enumerate(path):
    if(image_name.split('.')[1]=='jpg'):
      image=cv2.imread(directory+sub_path+image_name)
      image=Image.fromarray(image,'RGB')
      image=image.resize((64,64))
      dataset.append(np.array(image))
      labels.append(label_data)

In [6]:
preprocessing(no_tumer_images,no_dir,0)
preprocessing(yes_tumer_images,yes_dir,1)

In [7]:
print(dataset)
print(labels)
print(len(dataset))
print(len(labels))

[array([[[28, 28, 28],
        [28, 28, 28],
        [28, 28, 28],
        ...,
        [28, 28, 28],
        [28, 28, 28],
        [28, 28, 28]],

       [[28, 28, 28],
        [28, 28, 28],
        [28, 28, 28],
        ...,
        [28, 28, 28],
        [28, 28, 28],
        [28, 28, 28]],

       [[28, 28, 28],
        [28, 28, 28],
        [28, 28, 28],
        ...,
        [28, 28, 28],
        [28, 28, 28],
        [28, 28, 28]],

       ...,

       [[28, 28, 28],
        [28, 28, 28],
        [28, 28, 28],
        ...,
        [28, 28, 28],
        [28, 28, 28],
        [28, 28, 28]],

       [[28, 28, 28],
        [28, 28, 28],
        [28, 28, 28],
        ...,
        [28, 28, 28],
        [28, 28, 28],
        [28, 28, 28]],

       [[28, 28, 28],
        [28, 28, 28],
        [28, 28, 28],
        ...,
        [28, 28, 28],
        [28, 28, 28],
        [28, 28, 28]]], dtype=uint8), array([[[28, 28, 28],
        [24, 24, 24],
        [25, 25, 25],
        ...,
        [25

### Data Reshaping


In [8]:
arr_dataset=np.array(dataset)
arr_labels=np.array(labels)

## Model Selection

In [9]:
X_train,X_test,y_train,y_test=train_test_split(arr_dataset,arr_labels,test_size=0.2)

In [10]:
X_train.shape
y_train.shape

(2400,)

In [11]:
x_train=tf.keras.utils.normalize(X_train, axis=1)
x_test=tf.keras.utils.normalize(X_test, axis=1)

#encoding
# y_train=tf.keras.utils.to_categorical(y_train,num_classes=2)
# y_test=tf.keras.utils.to_categorical(y_test,num_classes=2)

## Model Building

In [12]:
model=Sequential()
model.add(Conv2D(filters=64, kernel_size=(3,3), input_shape=(X_train.shape[1], X_train.shape[2], 3)))
model.add(Activation('relu'))
model.add(MaxPooling2D(pool_size=(2,2)))

model.add(Conv2D(filters=32, kernel_size=(3,3), kernel_initializer='he_uniform'))
model.add(Activation('relu'))
model.add(MaxPooling2D(pool_size=(2,2)))

model.add(Conv2D(filters=64, kernel_size=(3,3), kernel_initializer='he_uniform'))
model.add(Activation('relu'))
model.add(MaxPooling2D(pool_size=(2,2)))

model.add(Conv2D(filters=128, kernel_size=(3,3), input_shape=(X_train.shape[1], X_train.shape[2], 3)))
model.add(Activation('relu'))
model.add(MaxPooling2D(pool_size=(2,2)))

model.add(Flatten())
model.add(Dense(units=64, activation='relu'))
model.add(Dropout(0.3))
model.add(Dense(units=16, activation='relu'))
model.add(Dropout(0.3))
model.add(Dense(units=1,activation='sigmoid'))
#model.add(Dense(units=2,activation='softmax')) => for encoded variables

model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'],run_eagerly=True)
model.summary()


Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 conv2d (Conv2D)             (None, 62, 62, 64)        1792      
                                                                 
 activation (Activation)     (None, 62, 62, 64)        0         
                                                                 
 max_pooling2d (MaxPooling2  (None, 31, 31, 64)        0         
 D)                                                              
                                                                 
 conv2d_1 (Conv2D)           (None, 29, 29, 32)        18464     
                                                                 
 activation_1 (Activation)   (None, 29, 29, 32)        0         
                                                                 
 max_pooling2d_1 (MaxPoolin  (None, 14, 14, 32)        0         
 g2D)                                                   

## Model Training

In [13]:
model.fit(x_train, y_train, verbose=1, epochs=15, validation_data=(x_test,y_test))

Epoch 1/15
75/75 [==============================] - 29s 377ms/step - loss: 0.6207 - accuracy: 0.6500 - val_loss: 0.5032 - val_accuracy: 0.7667
Epoch 2/15
75/75 [==============================] - 27s 354ms/step - loss: 0.4899 - accuracy: 0.7854 - val_loss: 0.4097 - val_accuracy: 0.8100
Epoch 3/15
75/75 [==============================] - 28s 372ms/step - loss: 0.3838 - accuracy: 0.8438 - val_loss: 0.4029 - val_accuracy: 0.8150
Epoch 4/15
75/75 [==============================] - 28s 375ms/step - loss: 0.3137 - accuracy: 0.8733 - val_loss: 0.3188 - val_accuracy: 0.8583
Epoch 5/15
75/75 [==============================] - 29s 389ms/step - loss: 0.2393 - accuracy: 0.9146 - val_loss: 0.2318 - val_accuracy: 0.9083
Epoch 6/15
75/75 [==============================] - 30s 396ms/step - loss: 0.1802 - accuracy: 0.9413 - val_loss: 0.1741 - val_accuracy: 0.9383
Epoch 7/15
75/75 [==============================] - 28s 373ms/step - loss: 0.1195 - accuracy: 0.9633 - val_loss: 0.2122 - val_accuracy: 0.9167

In [14]:
model.save("Brain_Tumor_Detection_Model.keras")

## Model Prediction

In [24]:
def predict_image(directory_path, sub_dir_path):
  for i, image_name in enumerate(directory_path):
    if image_name.split('.')[1] == 'jpg':
      image = cv2.imread(directory+sub_dir_path+image_name)
      image = Image.fromarray(image, 'RGB')
      image = image.resize((64, 64))
      image = np.array(image)
      image = tf.keras.utils.normalize(image, axis=1)
      prediction = model.predict(np.array([image]))
      if prediction[0] > 0.5:
        print("Yes, there is a tumor")
      else:
        print("No, there is no tumor")

In [25]:
dir_path='/content/Brain_Tumor/Brain_Tumor/'
dir_sub_path=os.listdir(dir_path + 'pred/')
# print(dir_sub_path)
sub_sub_path='pred/'
predict_image(dir_sub_path,sub_sub_path)

1/1 [==============================] - 0s 35ms/step
Yes, there is a tumor
1/1 [==============================] - 0s 32ms/step
No, there is no tumor
1/1 [==============================] - 0s 31ms/step
Yes, there is a tumor
1/1 [==============================] - 0s 30ms/step
Yes, there is a tumor
1/1 [==============================] - 0s 30ms/step
Yes, there is a tumor
1/1 [==============================] - 0s 31ms/step
No, there is no tumor
1/1 [==============================] - 0s 31ms/step
Yes, there is a tumor
1/1 [==============================] - 0s 32ms/step
No, there is no tumor
1/1 [==============================] - 0s 32ms/step
No, there is no tumor
1/1 [==============================] - 0s 32ms/step
No, there is no tumor
1/1 [==============================] - 0s 33ms/step
No, there is no tumor
1/1 [==============================] - 0s 30ms/step
No, there is no tumor
1/1 [==============================] - 0s 40ms/step
No, there is no tumor
1/1 [==============================] -